In [ ]:
from ngsolve import *
from netgen.geom2d import SplineGeometry
from ngsolve.webgui import Draw
from netgen.occ import *
from netgen.webgui import Draw as DrawGeo
shape = Rectangle(2,2).Face().Move((-1,-1,0))
shape.edges.Min(X).name="left"
shape.edges.Max(X).name="right"
shape.edges.Min(Y).name="bottom"
shape.edges.Max(Y).name="top"

time = 0.0
dt = 0.001

mesh = Mesh(OCCGeometry(shape, dim=2).GenerateMesh(maxh=0.25))



def Solve(gfu, fes, u, v):
    b = CoefficientFunction((2*y*(1-x*x),-2*x*(1-y*y)))
    a = BilinearForm(fes, symmetric=False)
    a += 0.01*grad(u)*grad(v)*dx + b*grad(u)*v*dx
    a.Assemble()
    m = BilinearForm(fes, symmetric=False)
    m += u*v*dx
    m.Assemble()
    mstar = m.mat.CreateMatrix()
    mstar.AsVector().data = m.mat.AsVector() + dt * a.mat.AsVector()
    invmstar = mstar.Inverse(freedofs=fes.FreeDofs())
    gaussp = exp(-6*((x+0.5)*(x+0.5)+y*y))-exp(-6*((x-0.5)*(x-0.5)+y*y))
    f = LinearForm(fes)
    f += gaussp*v*dx
    f.Assemble()
    res = dt * f.vec - dt * a.mat * gfu.vec
    gfu.vec.data += invmstar * res
    return gfu

space_flux = HDiv(mesh, order=2, autoupdate=True)
gf_flux = GridFunction(space_flux, "flux", autoupdate=True)

def CalcError(gfu, fes, new_mesh):
    flux = 0.01 * grad(gfu)
    # interpolate finite element flux into H(div) space:
    gf_flux.Set (flux)

    # Gradient-recovery error estimator
    err = 1/0.01*(flux-gf_flux)*(flux-gf_flux)
    elerr = Integrate (err, new_mesh, VOL, element_wise=True)

    maxerr = max(elerr)
    #print ("maxerr = ", maxerr)

    for el in new_mesh.Elements():
        new_mesh.SetRefinementFlag(el, elerr[el.nr] > 0.25*maxerr)
    return new_mesh


def TimeStepping(initial_cond = None, t0 = 0, tend = 2,
                 nsamples = 10):
    if initial_cond:
        fes = H1(Mesh(mesh.ngmesh.Copy()), order=3, dirichlet="bottom|right|left|top", autoupdate=True)
        gfu = GridFunction(fes, autoupdate=True)
        gfu.Set(initial_cond)
    cnt = 0; time = t0
    sample_int = int(floor(tend / dt / nsamples)+1)
    gfut = GridFunction(gfu.space,multidim=0)
    gfut.AddMultiDimComponent(gfu.vec)
    while time < tend - 0.5 * dt:
        new_mesh = Mesh(mesh.ngmesh.Copy())
        fes = H1(new_mesh, order=3, dirichlet="bottom|right|left|top", autoupdate=True)
        u,v = fes.TnT()
        with TaskManager():
            while fes.ndof < 100000:
                Solve(gfu, fes, u, v)
                CalcError(gfu, fes, new_mesh)
                new_mesh.Refine()
        #Solve(gfu, fes, u, v)


        print("\r",time,end="")

        if cnt % sample_int == 0:
            gfut.AddMultiDimComponent(gfu.vec)
        cnt += 1; time = cnt * dt
    return gfut, new_mesh

gfut, new_mesh = TimeStepping((1-y*y)*x)

Draw(gfut, new_mesh, interpolate_multidim=True, animate=True)
